# Import libraries, set options, connect to DB

In [1]:
# Configuration code for datawrangling
import pandas as pd
import os
import numpy as np
from datetime import datetime
from geocode import geocode
import mapToPoly
from mapToPoly import mapToPoly
pd.set_option('display.max_row', 30000)
import csv

# Configuration code in order to connect to the database
from sqlalchemy import create_engine, exists
from sqlalchemy.orm import sessionmaker
from database_setup_cloud import MixpanelMap, Base

passWord = os.environ['totagoPassWord']
# This commented out one was how I connected to the remote database
DATABASE_URI = 'postgres://awsuser:' + passWord + '@totago-staging-06-28-19.cjtqfbi6mrth.us-west-2.rds.amazonaws.com:5432/totago'

# This code was how I connected to the local database
# DATABASE_URI = 'postgres+psycopg2://maxcarey:' + passWord + '@localhost:5432/totago'
engine = create_engine(DATABASE_URI)

#engine = create_engine('sqlite:///totagoData.db')

# Bind the engine to the metadata of the Base class so that the
# declaratives can be accessed through a DBSession instance
Base.metadata.bind = engine

DBSession = sessionmaker(bind=engine)

session = DBSession()

/Library/Frameworks/Python.framework/Versions/3.6/lib/python3.6/site-packages/psycopg2/__init__.py:144: UserWarning: The psycopg2 wheel package will be renamed from release 2.8; in order to keep installing from binary please use "pip install psycopg2-binary" instead. For details see: <http://initd.org/psycopg/docs/install.html#binary-install-from-pypi>.
  """)


# Read in data as pandas data frame, selecting only certain fields

In [2]:
fields = ['distinct_id', 'numItinerariesReturned', 'departureDate', 'startFromLocation', 'selectedDestination_id', 'selectedDestination_name', 'time', 'user_id']

In [3]:
df = pd.read_csv('modified_iten.csv', usecols = fields, dtype={"selectedDestination_id" : "str"})

# Wrange field: destinationIDs

In [4]:
# Replace all of the NAs for destinationIDs with 0
df.selectedDestination_id.fillna(0, inplace = True)

## Remove the 2 cases where the string says null
## Great tutorial here: https://www.youtube.com/watch?v=2AFGPdNn4FM
df = df[df.selectedDestination_id != 'null']

## Convert destinationIDs column to an integer value
df['selectedDestination_id'] = df.selectedDestination_id.astype(int)

# Wrangle field: numItenerariesReturned

In [5]:
# Replace all of the NAs for numItinerariesReturned with 1
df.numItinerariesReturned.fillna(1, inplace = True)

# Convert from float to integer
df['numItinerariesReturned'] = df.numItinerariesReturned.astype(int)

# Select, only observatiosn where this field is greater than 0 (now that the NAs are gone)


# Wrangle Field: Destination Name

In [6]:
#Convert this field to an integer replacing all NA's with zero
# This gets rid of the trailing zeros
df.selectedDestination_name.fillna("", inplace = True)

# Wrangle Field: departureDate

In [7]:
#Convert destinationIDs column to an integer value
# It looks like there were some complex rows being held in here before, I thought that when df.dtypes returned object that
# meant string but apprently not
df['departureDate'] = df.departureDate.astype(str)

print("number of rows before removal of anamoulous departureDate cases")
print(len(df))

# IT looks like there are some cases where this field is blank, says nan, is in format 24503, or in format "masked" 
# We need to remove these cases from the data frame
# I can see that some blank rows are still printed out.
df = df[df.departureDate != '']
df = df[df.departureDate != 'nan']
df = df[df.departureDate != '24503']
df = df[df.departureDate != '[masked]']

print("number of rows after removal of anamoulous departureDate cases")
print(len(df))

# Create a function extractDate that extracts the first ten characters of an input string
def extractDate(dateString):
    extractedDate = dateString[0:10]
    if len(extractedDate) < 10:
        print(extractedDate)
    return extractedDate

''' Code to test if the extractDate function works

# Apply this function to create  a new column
df['departureDateFixed'] = df.departureDate.apply(extractDate)

cols = ['distinct_id', 'departureDate', 'departureDateFixed', 'numItinerariesReturned', 'selectedDestination_id', 'selectedDestination_name', 'startFromLocation']

df = df[cols]
'''

# Override departure date extracting all of the null time stamps
df['departureDate'] = df.departureDate.apply(extractDate)


# Convert departure date into a time object in pandas
#See here: https://stackoverflow.com/questions/26763344/convert-pandas-column-to-datetime
# Though this actually might not need to be done
#df['departureDate'] = df.departureDate.apply(lambda x: datetime.strptime(x, '%Y-%m-%d'))




#df['departureDate'] = datetime.strptime(df['departureDate'], '%Y-%m-%-d')  
#df['departureDate'] = pd.to_datetime(df['departureDate'], format = '%Y-%m-%-d')



number of rows before removal of anamoulous departureDate cases
36968
number of rows after removal of anamoulous departureDate cases
36960


# Wrangle Field: distinctID

In [8]:
# Create a coloumn that combines the unix time stamp with distinct_id so that we have a primary key for database
df["primary_key"] = df["distinct_id"] + "-" + df["time"].map(str)
vc = df.primary_key.value_counts()
unique_keys = df.primary_key.unique()

# Wrangle user_id field

In [9]:
df.dtypes

departureDate                object
distinct_id                  object
numItinerariesReturned        int64
selectedDestination_id        int64
selectedDestination_name     object
startFromLocation            object
time                          int64
user_id                     float64
primary_key                  object
dtype: object

In [10]:
# This gets rid of the railing zeros and all of the nas are just
# blank

df['user_id'] = df['user_id'].fillna(0).astype(np.int64)

#Convert to string to be consistent with other fields in database
df['user_id'] = df['user_id'].astype(str)


# Create a subset of the datle with sample method to test geocode and database entry logic

In [11]:
# Create a random sample of the database, these entries will be added to the database in the next section
sampleDf = df.tail(5000)

# Output this random sample
sampleDf.head(len(sampleDf))

departureDate                                        distinct_id  \
31968    2019-06-22  16b7c2708b7f1c-0bbd673044c00e8-6427872-5a900-1...   
31969    2019-06-23  16b82c05e2c95c-09441f00c28672-37677e02-13c680-...   
31970    2019-06-23  16b82c05e2c95c-09441f00c28672-37677e02-13c680-...   
31971    2019-06-23  16b82c2f0ba5c6-0222b0d0ddb6f18-6427872-4a574-1...   
31972    2019-06-23  16b82d273aa275-07180d8243146f-2e064a75-100200-...   
31973    2019-06-23  16b82e112fb25e-0630c1fc4011ac-1f333f32-59b90-1...   
31974    2019-06-23  16b82e112fb25e-0630c1fc4011ac-1f333f32-59b90-1...   
31975    2019-06-23  16b82d273aa275-07180d8243146f-2e064a75-100200-...   
31976    2019-06-23  16b82e112fb25e-0630c1fc4011ac-1f333f32-59b90-1...   
31977    2019-06-23               abfc5c20-18b4-4637-af1f-f1fb3ec67f7d   
31978    2019-06-23  16b5c4ea243239-0407e95b31ab9a-3d176e50-4a640-1...   
31979    2019-06-23  16b5c4ea243239-0407e95b31ab9a-3d176e50-4a640-1...   
31980    2019-06-23  16b5c4ea243239-0407e95b31ab9a-3d176e50-4a640-1...   
31981    2019-06-23  16b82e112fb25e-0630c1fc4011ac-1f333f32-59b90-1...   
31982    2019-06-29  16b82f68164e82-061b3dc52209e4-37607603-1aeaa0-...   
31983    2019-06-29  16b82fe251b69e-09959c6256c5098-3d176e50-3d10d-...   
31984    2019-06-23  16b8323606c144-0990cb1bc27bec-4f3b6153-4b6a2-1...   
31985    2019-06-23  16b8323606c144-0990cb1bc27bec-4f3b6153-4b6a2-1...   
31986    2019-06-23  16b8323606c144-0990cb1bc27bec-4f3b6153-4b6a2-1...   
31987    2019-06-23  16b8323606c144-0990cb1bc27bec-4f3b6153-4b6a2-1...   
31988    2019-06-23  16b8323606c144-0990cb1bc27bec-4f3b6153-4b6a2-1...   
31989    2019-06-23  16b8323606c144-0990cb1bc27bec-4f3b6153-4b6a2-1...   
31990    2019-06-23  16b8323606c144-0990cb1bc27bec-4f3b6153-4b6a2-1...   
31991    2019-06-23  16b8323606c144-0990cb1bc27bec-4f3b6153-4b6a2-1...   
31992    2019-06-24               b5101505-0482-4056-99ef-e0977c228121   
31993    2019-06-27  16b24a1b80da86-0bddace37cf026-3e176b5a-4a640-1...   
31994    2019-06-23  16b84a341d88a6-0695dff2b28d76-6427872-4a574-16...   
31995    2019-06-23  16b84cc033b73d-071c9e052eb441-734c1551-2c600-1...   
31996    2019-06-24  16b24a1b80da86-0bddace37cf026-3e176b5a-4a640-1...   
31997    2019-06-23  16b84ea57e93d-065b1d6db54cee-16294479-55188-16...   
31998    2019-06-23  16b8528ee471bb-05c79891e078d2-784a5037-100200-...   
31999    2019-06-24  16b85421f9b30c-014d5ee57a43d38-2d6a4e35-3d10d-...   
32000    2019-06-23  16b8544a95a935-0cb89a92bf1ea98-10073e7b-f31d4-...   
32001    2019-06-23  16b82c05e2c95c-09441f00c28672-37677e02-13c680-...   
32002    2019-06-23  16b82c05e2c95c-09441f00c28672-37677e02-13c680-...   
32003    2019-06-23  16b82c05e2c95c-09441f00c28672-37677e02-13c680-...   
32004    2019-06-23  16b82c05e2c95c-09441f00c28672-37677e02-13c680-...   
32005    2019-06-23  16b855d5cdd236-089fc4dab6fc3e-37677e04-13c680-...   
32006    2019-06-23  16b855d5cdd236-089fc4dab6fc3e-37677e04-13c680-...   
32007    2019-06-23  16b855d5cdd236-089fc4dab6fc3e-37677e04-13c680-...   
32008    2019-06-23  16b855d5cdd236-089fc4dab6fc3e-37677e04-13c680-...   
32009    2019-06-23  16b85811b3c96-07081ba9a4677-784a5037-280000-16...   
32010    2019-06-23  16b7c2708b7f1c-0bbd673044c00e8-6427872-5a900-1...   
32011    2019-06-23  16b7c2708b7f1c-0bbd673044c00e8-6427872-5a900-1...   
32012    2019-06-23  16b85e342e347c-0ce6607b10147d-e343166-13c680-1...   
32013    2019-06-23  16b85f2d9083bf-023c120fe8dcfc-3e176e50-4a640-1...   
32014    2019-06-23  16b85f2d9083bf-023c120fe8dcfc-3e176e50-4a640-1...   
32015    2019-06-23  16b353bd946539-0151b46cf361ae8-734c1451-3d10d-...   
32016    2019-06-23  16b85f2d9083bf-023c120fe8dcfc-3e176e50-4a640-1...   
32017    2019-06-23               abfc5c20-18b4-4637-af1f-f1fb3ec67f7d   
32018    2019-06-25  16b8634ecf91-0479735ff98b45-3606340-49a10-16b8...   
32019    2019-06-23  16b85f2d9083bf-023c120fe8dcfc-3e176e50-4a640-1...   
32020    2019-06-23  16b86f5fc7be4-076752d9e53c0b-e343166-100200-16...   
32021    2

## Read in the destination data to allow the possibility to pull the correct names

 


In [12]:
sampleDf.dtypes

departureDate               object
distinct_id                 object
numItinerariesReturned       int64
selectedDestination_id       int64
selectedDestination_name    object
startFromLocation           object
time                         int64
user_id                     object
primary_key                 object
dtype: object

# Loop through the rows in the dataframe, geocode, add entry to database

In [13]:
# Loop through the subsetted pandas data frame

# Uncomment the code below to loop through the the sample data frame
# for index, row in sampleDf.iterrows():

for index, row in sampleDf.iterrows():
  

    # Pull out the primary key into a variable
    testKey = row["primary_key"]
    
    # Check to see if that distinctID is in the data base
    # See this post: https://stackoverflow.com/questions/6587879/how-to-elegantly-check-the-existence-of-an-object-instance-variable-and-simultan?utm_medium=organic&utm_source=google_rich_qa&utm_campaign=google_rich_qa
    entryExists = session.query(exists().where(MixpanelMap.distinctkey==testKey)).scalar()

    # If the entry is not in the database
    if not entryExists:
    
        # Get the string to be geocoded
        locationToGeocode = row["startFromLocation"]

        # In the case that the desintaiton ID is zero, this means it was an NA
        # So don't even try to geocode
        
        if row["selectedDestination_id"] != 0:
        
            # Try to run the geocode function that returns a dictionary of information
            try:
                geocodeInfo = geocode(locationToGeocode)
                # If geocoding works, set valid to tre
                valid = True

            # If the geocode function doesn't work set valid to false
            except:
                valid = False
        
        # In the case that the selected Destination ID is 0 then set valid to false
        else:
            valid=False

        # If valid is true create a database entry with information from the dataframe, and the returned geocode informaiton
        if valid:
            
            # Sometimes, such as when a generic city is sent to the geocode() function a geometric center
            # is returned, this means there is no postal code
            
            # In this case, we can set the postalCode to none
            if not 'postalCode' in geocodeInfo:
                geocodeInfo['postalCode'] = "none"

            
            # Mapp the gps coordinates returned to the zip code polygons
            zipCodeInfo = mapToPoly(geocodeInfo['lat'], geocodeInfo['lng'], 'postal')
            
            
            if zipCodeInfo:
                zipCodeMapped = zipCodeInfo[0]
                region = zipCodeInfo[1]
            else:
                zipCodeMapped = 'outsideRegion'
                zipCodeMapped = 'outsideRegion'
            
            barrioInfo = mapToPoly(geocodeInfo['lat'], geocodeInfo['lng'], 'barrio')
            print(barrioInfo)
            
            if barrioInfo:
                barrioMapped = barrioInfo
            else:
                barrioMapped = 'outsideRegion'
                
            ## Get selected Destination Names
            # Pull the selected destination name
            selectedDestinationName = row["selectedDestination_name"]
            
            
            #if not selectedDestinationName:
            #    
            #    key = str(row["selectedDestination_id"])
            #    
            #    if key in destinations:
            #
            #        # Pull the data out from the dictionary that was created in the cell above
            #        newName = destinations[str(row["selectedDestination_id"])]['name']
        #
            #        # Add the new name to the new row
            #        selectedDestinationName  = newName
            #
            #    # In the case that there is destination that corresponds mark
            #    else:
            #    
            #        # TODO: CONSIDER CHANGING THE NAME OF THIS TO SOMETHING ELSE
            #        selectedDestinationName = "DELETED"
            #        # And overwrite valid to false at this point because there is no destination
            #        valid = False
            
            databaseEntry = MixpanelMap(distinctkey=row["primary_key"],
                                      numberitinerariesreturned=row["numItinerariesReturned"],
                                      selecteddestination_id=row["selectedDestination_id"],
                                      selecteddestination_name=selectedDestinationName,
                                      startfromlocation=row["startFromLocation"],
                                      departuredate=row["departureDate"],
                                      # Get data from python dictionary returned from geocode() function
                                      formatted_address=geocodeInfo['formatted_address'],
                                      lat=geocodeInfo['lat'],
                                      lng=geocodeInfo['lng'],
                                      postalcode=geocodeInfo['postalCode'],
                                      postalcodemapped=zipCodeMapped,
                                      barriomapped=barrioMapped,
                                      userid=row["user_id"],
                                      region=region,
                                      valid=valid)
        # If valid is false, just fill in the information that we have from the pandas data frame
        else:
            databaseEntry = MixpanelMap(distinctkey=row["primary_key"],
                                      numberitinerariesreturned=row["numItinerariesReturned"],
                                      selecteddestination_id=row["selectedDestination_id"],
                                      selecteddestination_name=row["selectedDestination_name"],
                                      startfromlocation=row["startFromLocation"],
                                      departuredate=row["departureDate"],
                                      userid=row["user_id"],
                                      valid=valid)

        # Add the the information to a database.    
        session.add(databaseEntry)
        session.commit()
    
    else:
        print("Entry already inside database")

{'formatted_address': '2202 8th Ave, Seattle, WA 98121, USA', 'lat': 47.617737, 'lng': -122.339418, 'postalCode': '98121'}
343995
{'formatted_address': '525 Boren Ave N, Seattle, WA 98109, USA', 'lat': 47.623719, 'lng': -122.3359958, 'postalCode': '98109'}
271987
{'formatted_address': '525 Boren Ave N, Seattle, WA 98109, USA', 'lat': 47.623719, 'lng': -122.3359958, 'postalCode': '98109'}
271987
{'formatted_address': '525 Boren Ave N, Seattle, WA 98109, USA', 'lat': 47.623719, 'lng': -122.3359958, 'postalCode': '98109'}
271987
{'formatted_address': '151 W Cordova St, Vancouver, BC V6B 1B2, Canada', 'lat': 49.2833614, 'lng': -123.1082318, 'postalCode': 'V6B 1B2'}
CBD
{'formatted_address': '112 N 83rd St, Seattle, WA 98103, USA', 'lat': 47.68932789999999, 'lng': -122.357322, 'postalCode': '98103'}
250788
{'formatted_address': '112 N 83rd St, Seattle, WA 98103, USA', 'lat': 47.68932789999999, 'lng': -122.357322, 'postalCode': '98103'}
250788
{'formatted_address': 'Vancouver, BC V7Y 1C6, Ca

{'formatted_address': '2202 8th Ave, Seattle, WA 98121, USA', 'lat': 47.617737, 'lng': -122.339418, 'postalCode': '98121'}
343995
{'formatted_address': '525 Boren Ave N, Seattle, WA 98109, USA', 'lat': 47.623719, 'lng': -122.3359958, 'postalCode': '98109'}
271987
{'formatted_address': 'Seattle, WA, USA', 'lat': 47.6062095, 'lng': -122.3320708}
271849
{'formatted_address': '2201 8th Ave, Seattle, WA 98121, USA', 'lat': 47.617208, 'lng': -122.3397187, 'postalCode': '98121'}
343995
{'formatted_address': '4305 Fleming St, Vancouver, BC V5N 3W4, Canada', 'lat': 49.2463266, 'lng': -123.0723672, 'postalCode': 'V5N 3W4'}
KC
{'formatted_address': '911 W Pender St, Vancouver, BC V6C 1L6, Canada', 'lat': 49.28630649999999, 'lng': -123.1168309, 'postalCode': 'V6C 1L6'}
CBD
{'formatted_address': '1006 Beach Ave, Vancouver, BC V6E 4M2, Canada', 'lat': 49.27583019999999, 'lng': -123.1348452, 'postalCode': 'V6E 4M2'}
CBD
{'formatted_address': '1006 Beach Ave, Vancouver, BC V6E 4M2, Canada', 'lat': 49.

{'formatted_address': 'Port Moody, BC, Canada', 'lat': 49.2849107, 'lng': -122.8677562}
None
{'formatted_address': '2026 Yale Ave E, Seattle, WA 98102, USA', 'lat': 47.6376149, 'lng': -122.3268133, 'postalCode': '98102'}
271857
{'formatted_address': '2026 Yale Ave E, Seattle, WA 98102, USA', 'lat': 47.6376149, 'lng': -122.3268133, 'postalCode': '98102'}
271857
{'formatted_address': '2026 Yale Ave E, Seattle, WA 98102, USA', 'lat': 47.6376149, 'lng': -122.3268133, 'postalCode': '98102'}
271857
{'formatted_address': '2026 Yale Ave E, Seattle, WA 98102, USA', 'lat': 47.6376149, 'lng': -122.3268133, 'postalCode': '98102'}
271857
{'formatted_address': '4th Ave &, Wall St, Seattle, WA 98121, United States', 'lat': 47.616689, 'lng': -122.346173, 'postalCode': '98121'}
271808
{'formatted_address': '206 Harvard Ave E, Seattle, WA 98102, USA', 'lat': 47.6202289, 'lng': -122.3219314, 'postalCode': '98102'}
250206
{'formatted_address': '206 Harvard Ave E, Seattle, WA 98102, USA', 'lat': 47.6202289

{'formatted_address': '2400 4th Ave, Seattle, WA 98121, USA', 'lat': 47.616916, 'lng': -122.3450867, 'postalCode': '98121'}
271808
{'formatted_address': '1296 Connaught Dr, Vancouver, BC V6H 2H2, Canada', 'lat': 49.2446034, 'lng': -123.1352406, 'postalCode': 'V6H 2H2'}
SHAU
{'formatted_address': '1296 Connaught Dr, Vancouver, BC V6H 2H2, Canada', 'lat': 49.2446034, 'lng': -123.1352406, 'postalCode': 'V6H 2H2'}
SHAU
{'formatted_address': '1820 Woodland Dr, Vancouver, BC V5N 3N7, Canada', 'lat': 49.2683942, 'lng': -123.073297, 'postalCode': 'V5N 3N7'}
GW
{'formatted_address': 'Lake Sammamish State Park, 2000 NW Sammamish Rd, Issaquah, WA 98027, USA', 'lat': 47.5590542, 'lng': -122.0563198, 'postalCode': '98027'}
None
{'formatted_address': 'Tacoma, WA, USA', 'lat': 47.2528768, 'lng': -122.4442906}
274674
{'formatted_address': 'Seattle, WA, USA', 'lat': 47.6062095, 'lng': -122.3320708}
271849
{'formatted_address': '701 W Georgia St, Vancouver, BC V7Y 1G5, Canada', 'lat': 49.2831244, 'lng':

{'formatted_address': '1425 Spring St, Seattle, WA 98104, USA', 'lat': 47.6115793, 'lng': -122.3214356, 'postalCode': '98104'}
271869
{'formatted_address': '1425 Spring St, Seattle, WA 98104, USA', 'lat': 47.6115793, 'lng': -122.3214356, 'postalCode': '98104'}
271869
{'formatted_address': '1425 Spring St, Seattle, WA 98104, USA', 'lat': 47.6115793, 'lng': -122.3214356, 'postalCode': '98104'}
271869
{'formatted_address': '1425 Spring St, Seattle, WA 98104, USA', 'lat': 47.6115793, 'lng': -122.3214356, 'postalCode': '98104'}
271869
{'formatted_address': '1425 Spring St, Seattle, WA 98104, USA', 'lat': 47.6115793, 'lng': -122.3214356, 'postalCode': '98104'}
271869
{'formatted_address': '1425 Spring St, Seattle, WA 98104, USA', 'lat': 47.6115793, 'lng': -122.3214356, 'postalCode': '98104'}
271869
{'formatted_address': '6200 University Blvd, Vancouver, BC V6T 1Z4, Canada', 'lat': 49.26506999999999, 'lng': -123.250572, 'postalCode': 'V6T 1Z4'}
None
{'formatted_address': '6200 University Blvd

...

{'formatted_address': '910 8th Ave, Seattle, WA 98104, USA', 'lat': 47.6075331, 'lng': -122.3277901, 'postalCode': '98104'}
271869
{'formatted_address': '910 8th Ave, Seattle, WA 98104, USA', 'lat': 47.6075331, 'lng': -122.3277901, 'postalCode': '98104'}
271869
{'formatted_address': '910 8th Ave, Seattle, WA 98104, USA', 'lat': 47.6075331, 'lng': -122.3277901, 'postalCode': '98104'}
271869
{'formatted_address': '910 8th Ave, Seattle, WA 98104, USA', 'lat': 47.6075331, 'lng': -122.3277901, 'postalCode': '98104'}
271869
{'formatted_address': '14623 NE 43rd Pl, Bellevue, WA 98007, USA', 'lat': 47.6483739, 'lng': -122.1452364, 'postalCode': '98007'}
271818
{'formatted_address': '14623 NE 43rd Pl, Bellevue, WA 98007, USA', 'lat': 47.6483739, 'lng': -122.1452364, 'postalCode': '98007'}
271818
{'formatted_address': '14623 NE 43rd Pl, Bellevue, WA 98007, USA', 'lat': 47.6483739, 'lng': -122.1452364, 'postalCode': '98007'}
271818
{'formatted_address': '14623 NE 43rd Pl, Bellevue, WA 98007, USA'

None
{'formatted_address': '2324 W Broadway, Vancouver, BC V6K 2E5, Canada', 'lat': 49.26361850000001, 'lng': -123.1583702, 'postalCode': 'V6K 2E5'}
KITS
{'formatted_address': '13360 King George Blvd, Surrey, BC V3T 0A2, Canada', 'lat': 49.203303, 'lng': -122.852525, 'postalCode': 'V3T 0A2'}
None
{'formatted_address': '601 W Waterfront Rd, Vancouver, BC V6B 1G1, Canada', 'lat': 49.2863128, 'lng': -123.1100914, 'postalCode': 'V6B 1G1'}
CBD
{'formatted_address': '28 Eihu Ln, Vancouver, BC V6G 1E4, Canada', 'lat': 49.29242790000001, 'lng': -123.1359843, 'postalCode': 'V6G 1E4'}
WE
{'formatted_address': '522 Federal Ave E, Seattle, WA 98102, USA', 'lat': 47.6238348, 'lng': -122.3185042, 'postalCode': '98102'}
250206
{'formatted_address': '252 E Woodstock Ave, Vancouver, BC V5W 1N1, Canada', 'lat': 49.2333709, 'lng': -123.1000052, 'postalCode': 'V5W 1N1'}
RP
{'formatted_address': '791 W Georgia St, Vancouver, BC V6C 2T4, Canada', 'lat': 49.28343539999999, 'lng': -123.1180976, 'postalCode': 

CBD
{'formatted_address': '700 5th Ave N, Seattle, WA 98109, USA', 'lat': 47.62595229999999, 'lng': -122.3465824, 'postalCode': '98109'}
271906
{'formatted_address': 'Portland, OR, USA', 'lat': 45.5051064, 'lng': -122.6750261}
None
{'formatted_address': '1415 5th Ave, Seattle, WA 98101, USA', 'lat': 47.6100157, 'lng': -122.3355485, 'postalCode': '98101'}
271849
{'formatted_address': '3000 NE 4th St, Renton, WA 98056, USA', 'lat': 47.489499, 'lng': -122.1754151, 'postalCode': '98056'}
240770
{'formatted_address': '4512 SE 4th St, Renton, WA 98059, USA', 'lat': 47.4799012, 'lng': -122.1582511, 'postalCode': '98059'}
623356
{'formatted_address': '426 Yale Ave N, Seattle, WA 98109, USA', 'lat': 47.6227974, 'lng': -122.3303112, 'postalCode': '98109'}
271987
{'formatted_address': 'Seattle, WA 98102, USA', 'lat': 47.6338217, 'lng': -122.3215448, 'postalCode': '98102'}
250206
{'formatted_address': '4200 Whitman Ct NE, Seattle, WA 98105, USA', 'lat': 47.6581367, 'lng': -122.3036396, 'postalCode

{'formatted_address': '1420 5th Ave, Seattle, WA 98101, USA', 'lat': 47.610653, 'lng': -122.333993, 'postalCode': '98101'}
271849
{'formatted_address': '6825 35th Ave NE, Seattle, WA 98115, USA', 'lat': 47.6783564, 'lng': -122.2906616, 'postalCode': '98115'}
251709
{'formatted_address': '6825 35th Ave NE, Seattle, WA 98115, USA', 'lat': 47.6783564, 'lng': -122.2906616, 'postalCode': '98115'}
251709
{'formatted_address': '6825 35th Ave NE, Seattle, WA 98115, USA', 'lat': 47.6783564, 'lng': -122.2906616, 'postalCode': '98115'}
251709
{'formatted_address': '6825 35th Ave NE, Seattle, WA 98115, USA', 'lat': 47.6783564, 'lng': -122.2906616, 'postalCode': '98115'}
251709
{'formatted_address': '600 Union St, Seattle, WA 98101, USA', 'lat': 47.610348, 'lng': -122.3334921, 'postalCode': '98101'}
271849
{'formatted_address': '600 Union St, Seattle, WA 98101, USA', 'lat': 47.610348, 'lng': -122.3334921, 'postalCode': '98101'}
271849
{'formatted_address': 'Vancouver, BC, Canada', 'lat': 49.2827291

{'formatted_address': 'Wesbrook Mall & UBC Bus Loop, University Endowment Lands, BC V6T 1W3, Canada', 'lat': 49.26764679999999, 'lng': -123.246514, 'postalCode': 'V6T 1W3'}
None
{'formatted_address': '6248 Wellington Ave, West Vancouver, BC V7W 2H4, Canada', 'lat': 49.369107, 'lng': -123.2820389, 'postalCode': 'V7W 2H4'}
None
{'formatted_address': '6248 Wellington Ave, West Vancouver, BC V7W 2H4, Canada', 'lat': 49.369107, 'lng': -123.2820389, 'postalCode': 'V7W 2H4'}
None
{'formatted_address': '6080 Minoru Blvd, Richmond, BC V6Y 4A8, Canada', 'lat': 49.16912319999999, 'lng': -123.1399588, 'postalCode': 'V6Y 4A8'}
None
{'formatted_address': '1905 NE Naomi Pl, Seattle, WA 98115, USA', 'lat': 47.6735363, 'lng': -122.3073018, 'postalCode': '98115'}
251709
{'formatted_address': '1905 NE Naomi Pl, Seattle, WA 98115, USA', 'lat': 47.6735363, 'lng': -122.3073018, 'postalCode': '98115'}
251709
{'formatted_address': '1905 NE Naomi Pl, Seattle, WA 98115, USA', 'lat': 47.6735363, 'lng': -122.3073